# Hyperparameter Optimization on Slurm via SubmitIt

This notebook serves as a quickstart guide for using the Ax library with the SubmitIt library in an ask-tell loop. [SubmitIt](https://github.com/facebookincubator/submitit/) is a Python toolbox for submitting jobs to [Slurm](https://slurm.schedmd.com/quickstart.html). 

The notebook demonstrates how to use the Ax client in an ask-tell loop where each trial is scheduled to run on a Slurm cluster asynchronously.

To use this script, run it on a slurm node either as an interactive notebook or export it as a Python script and run it as a Slurm job.

## Importing Necessary Libraries
Let's start by importing the necessary libraries.

In [1]:
import time
from ax.service.ax_client import AxClient, ObjectiveProperties
from ax.utils.notebook.plotting import render
from ax.service.utils.report_utils import exp_to_df
from submitit import AutoExecutor, LocalJob, DebugJob

## Defining the Function to Optimize
We'll define a simple function to optimize. This function takes two parameters, and returns a single metric.

In [2]:
def evaluate(parameters):
    x = parameters["x"]
    y = parameters["y"]
    return {"result": (x - 3)**2 + (y - 4)**2}

Note: SubmitIt's [CommandFunction](https://github.com/facebookincubator/submitit/blob/main/docs/examples.md#working-with-commands) allows you to define commands to run on the node and then redirects the standard output.

## Setting up Ax
We'll use Ax's Service API for this example. We start by initializing an AxClient and creating an experiment.

In [3]:
ax_client = AxClient()
ax_client.create_experiment(
    name="my_experiment",
    parameters=[
        {"name": "x", "type": "range", "bounds": [-10.0, 10.0]},
        {"name": "y", "type": "range", "bounds": [-10.0, 10.0]},
    ],
    objectives={"result": ObjectiveProperties(minimize=True)},
    parameter_constraints=["x + y <= 2.0"],  # Optional.
)

[INFO 03-01 16:43:53] ax.service.ax_client: Starting optimization with verbose logging. To disable logging, set the `verbose_logging` argument to `False`. Note that float values in the logs are rounded to 6 decimal points.


[INFO 03-01 16:43:53] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x. If that is not the expected value type, you can explicitly specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.


[INFO 03-01 16:43:53] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter y. If that is not the expected value type, you can explicitly specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.


[INFO 03-01 16:43:53] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[-10.0, 10.0]), RangeParameter(name='y', parameter_type=FLOAT, range=[-10.0, 10.0])], parameter_constraints=[ParameterConstraint(1.0*x + 1.0*y <= 2.0)]).


[INFO 03-01 16:43:53] ax.modelbridge.dispatch_utils: Using Models.BOTORCH_MODULAR since there is at least one ordered parameter and there are no unordered categorical parameters.


[INFO 03-01 16:43:53] ax.modelbridge.dispatch_utils: Calculating the number of remaining initialization trials based on num_initialization_trials=None max_initialization_trials=None num_tunable_parameters=2 num_trials=None use_batch_trials=False


[INFO 03-01 16:43:53] ax.modelbridge.dispatch_utils: calculated num_initialization_trials=5


[INFO 03-01 16:43:53] ax.modelbridge.dispatch_utils: num_completed_initialization_trials=0 num_remaining_initialization_trials=5


[INFO 03-01 16:43:53] ax.modelbridge.dispatch_utils: `verbose`, `disable_progbar`, and `jit_compile` are not yet supported when using `choose_generation_strategy` with ModularBoTorchModel, dropping these arguments.


[INFO 03-01 16:43:53] ax.modelbridge.dispatch_utils: Using Bayesian Optimization generation strategy: GenerationStrategy(name='Sobol+BoTorch', steps=[Sobol for 5 trials, BoTorch for subsequent trials]). Iterations after 5 will take longer to generate due to model-fitting.


Other commonly used [parameters types](https://ax.dev/docs/glossary.html#parameter) include `choice` parameters and `fixed` parameters. 

Tip 1: you can specify additional information for parameters such as `log_scale`, if a parameter operates at a log-scale and `is_ordered` for choice parameters that have a meaningful ordering.

Tip 2: Ax is an excellent choice for multi-objective optimization problems when there are multiple competing objectives and the goal is to find all Pareto-optimal solutions.

Tip 3: One can define constraints on both the parameters and the outcome.

## Setting up SubmitIt
We'll use SubmitIt's `AutoExecutor` for this example. We start by initializing an `AutoExecutor`, and setting a few commonly used parameters.

In [4]:
# Log folder and cluster. Specify cluster='local' or cluster='debug' to run the jobs locally during development.
# When we're are ready for deployment, switch to cluster='slurm' 
executor = AutoExecutor(folder="/tmp/submitit_runs", cluster='debug') 
executor.update_parameters(timeout_min=60) # Timeout of the slurm job. Not including slurm scheduling delay.
executor.update_parameters(cpus_per_task=2)

Other commonly used Slurm parameters include `partition`, `ntasks_per_node`, `cpus_per_task`, `cpus_per_gpu`, `gpus_per_node`, `gpus_per_task`, `qos`, `mem`, `mem_per_gpu`, `mem_per_cpu`, `account`.

## Running the Optimization Loop
Now, we're ready to run the optimization loop. We'll use an ask-tell loop, where we ask Ax for a suggestion, evaluate it using our function, and then tell Ax the result.

The example loop schedules new jobs whenever there is availability. For tasks that take a similar amount of time regardless of the parameters, it may make more sense to wait for the whole batch to finish before scheduling the next (so ax can make better informed parameter choices).

Note that `get_next_trials` may not use all available `num_parallel_jobs` if it doesn't have good parameter candidates to run.

In [5]:
total_budget = 10
num_parallel_jobs = 3

jobs = []
submitted_jobs = 0
# Run until all the jobs have finished and our budget is used up.
while submitted_jobs < total_budget or jobs:
    for job, trial_index in jobs[:]:
        # Poll if any jobs completed
        # Local and debug jobs don't run until .result() is called.
        if job.done() or type(job) in [LocalJob, DebugJob]:
            result = job.result()
            ax_client.complete_trial(trial_index=trial_index, raw_data=result)
            jobs.remove((job, trial_index))
    
    # Schedule new jobs if there is availablity
    trial_index_to_param, _ = ax_client.get_next_trials(
        max_trials=min(num_parallel_jobs - len(jobs), total_budget - submitted_jobs))
    for trial_index, parameters in trial_index_to_param.items():
        job = executor.submit(evaluate, parameters)
        submitted_jobs += 1
        jobs.append((job, trial_index))
        time.sleep(1)
    
    # Display the current trials.
    display(exp_to_df(ax_client.experiment))

    # Sleep for a bit before checking the jobs again to avoid overloading the cluster. 
    # If you have a large number of jobs, consider adding a sleep statement in the job polling loop aswell.
    time.sleep(30)

[INFO 03-01 16:43:54] ax.service.ax_client: Generated new trial 0 with parameters {'x': 8.051495, 'y': -9.879305} using model Sobol.


[INFO 03-01 16:43:54] ax.service.ax_client: Generated new trial 1 with parameters {'x': 2.964798, 'y': -1.72008} using model Sobol.


[INFO 03-01 16:43:54] ax.service.ax_client: Generated new trial 2 with parameters {'x': -4.082544, 'y': -2.289171} using model Sobol.


[WARNING 03-01 16:43:57] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


[INFO 03-01 16:43:57] ax.service.utils.report_utils: No results present for the specified metrics `[Metric('result')]`. Returning arm parameters and metadata only.


...

trial_index arm_name trial_status generation_method      result         x  \
0            0      0_0    COMPLETED             Sobol  218.152703  8.051495   
1            1      1_0    COMPLETED             Sobol   32.720559  2.964798   
2            2      2_0    COMPLETED             Sobol   89.716105 -4.082544   
3            3      3_0    COMPLETED             Sobol  153.540973  1.162034   
4            4      4_0    COMPLETED             Sobol   77.321736  0.120051   
5            5      5_0    COMPLETED           BoTorch   12.607630  0.731981   
6            6      6_0    COMPLETED           BoTorch   12.625322  0.750322   
7            7      7_0    COMPLETED           BoTorch   12.636483  0.761230   
8            8      8_0      RUNNING           BoTorch         NaN  1.163757   
9            9      9_0      RUNNING           BoTorch         NaN -5.779644   

          y  
0 -9.879305  
1 -1.720080  
2 -2.289171  
3 -8.254095  
4 -4.308287  
5  1.268019  
6  1.249678  
7  1.238770  
8  0.836243  
9  7.779644

[INFO 03-01 16:46:23] ax.service.ax_client: Completed trial 8 with data: {'result': (13.381147, None)}.


[INFO 03-01 16:46:23] ax.service.ax_client: Completed trial 9 with data: {'result': (91.367867, None)}.


[WARNING 03-01 16:46:23] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


trial_index arm_name trial_status generation_method      result         x  \
0            0      0_0    COMPLETED             Sobol  218.152703  8.051495   
1            1      1_0    COMPLETED             Sobol   32.720559  2.964798   
2            2      2_0    COMPLETED             Sobol   89.716105 -4.082544   
3            3      3_0    COMPLETED             Sobol  153.540973  1.162034   
4            4      4_0    COMPLETED             Sobol   77.321736  0.120051   
5            5      5_0    COMPLETED           BoTorch   12.607630  0.731981   
6            6      6_0    COMPLETED           BoTorch   12.625322  0.750322   
7            7      7_0    COMPLETED           BoTorch   12.636483  0.761230   
8            8      8_0    COMPLETED           BoTorch   13.381147  1.163757   
9            9      9_0    COMPLETED           BoTorch   91.367867 -5.779644   

          y  
0 -9.879305  
1 -1.720080  
2 -2.289171  
3 -8.254095  
4 -4.308287  
5  1.268019  
6  1.249678  
7  1.238770  
8  0.836243  
9  7.779644


## Finally

We can retrieve the best parameters and render the response surface.

In [6]:
best_parameters, (means, covariances) = ax_client.get_best_parameters()
print(f'Best set of parameters: {best_parameters}')
print(f'Mean objective value: {means}')
# The covariance is only meaningful when multiple objectives are present.

render(ax_client.get_contour_plot())


[INFO 03-01 16:46:54] ax.service.ax_client: Retrieving contour plot with parameter 'x' on X-axis and 'y' on Y-axis, for metric 'result'. Remaining parameters are affixed to the middle of their range.


Best set of parameters: {'x': 1.163756981782356, 'y': 0.8362430182169049}
Mean objective value: {'result': 13.246586374701863}
